In [17]:
""" Convert RDS table to csv files on S3 and GCS
-------------------------------------------------------------------------------

After the files are stored on GCS, use the BigQuery Web UI to load the csv 
files in a table. 

Author: Rutger Hofste
Date: 20180712
Kernel: python35
Docker: rutgerhofste/gisdocker:ubuntu16.04
"""

# imports
import re
import os
import numpy as np
import pandas as pd
from retrying import retry
from datetime import timedelta
from sqlalchemy import *
pd.set_option('display.max_columns', 500)
import multiprocessing

SCRIPT_NAME = 'Y2018M07D17_RH_RDS_To_S3_V01'
OUTPUT_VERSION = 2

TESTING = 0

DATABASE_ENDPOINT = "aqueduct30v05.cgpnumwmfcqc.eu-central-1.rds.amazonaws.com"
DATABASE_NAME = "database01"

INPUT_TABLE_NAME = "y2018m07d30_rh_coalesce_columns_v01_v01"



ec2_output_path = "/volumes/data/{}/output_V{:02.0f}/".format(SCRIPT_NAME,OUTPUT_VERSION)
s3_output_path = "s3://wri-projects/Aqueduct30/processData/{}/output_V{:02.0f}/".format(SCRIPT_NAME,OUTPUT_VERSION)
gcs_output_path = "gs://aqueduct30_v01/{}/output_V{:02.0f}/".format(SCRIPT_NAME,OUTPUT_VERSION)

print("Input Table: " , INPUT_TABLE_NAME,
      "\nOutput ec2: ", ec2_output_path,
      "\nOutput s3: " , s3_output_path,
      "\nOutput gcs: ", gcs_output_path)

Input Table:  y2018m07d12_rh_ws_categorization_label_postgis_v01_v04 
Output ec2:  /volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/ 
Output s3:  s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/ 
Output gcs:  gs://aqueduct30_v01/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/


In [2]:
import time, datetime, sys
dateString = time.strftime("Y%YM%mD%d")
timeString = time.strftime("UTC %H:%M")
start = datetime.datetime.now()
print(dateString,timeString)
sys.version

Y2018M07D17 UTC 11:49


'3.5.4 |Anaconda, Inc.| (default, Nov 20 2017, 18:44:38) \n[GCC 7.2.0]'

In [3]:
!rm -r {{ec2_output_path}
!mkdir -p {ec2_output_path}

rm: cannot remove '{{ec2_output_path}': No such file or directory


In [4]:
F = open("/.password","r")
password = F.read().splitlines()[0]
F.close()

engine = create_engine("postgresql://rutgerhofste:{}@{}:5432/{}".format(password,DATABASE_ENDPOINT,DATABASE_NAME))

In [5]:
cpu_count = multiprocessing.cpu_count()
print("Power to the maxxx:", cpu_count)

Power to the maxxx: 16


In [6]:
sql = "SELECT DISTINCT pfafid_30spfaf06 FROM {} ORDER BY pfafid_30spfaf06".format(INPUT_TABLE_NAME)

In [7]:
df = pd.read_sql(sql,engine)

In [20]:
df.shape

(16385, 1)

In [8]:
df.head()

pfafid_30spfaf06
0            111011
1            111012
2            111013
3            111014
4            111015

In [9]:
if TESTING:
    df = df[0:10]

In [10]:
df_split = np.array_split(df, cpu_count*100)

In [11]:
def basin_to_csv(df):
    for index, row in df.iterrows():
        pfafid = row["pfafid_30spfaf06"]
        sql = "SELECT * FROM {} WHERE pfafid_30spfaf06 = {}".format(INPUT_TABLE_NAME,pfafid)
        df_basin = pd.read_sql(sql,engine)
        now = datetime.datetime.now()
        df_basin["processed_timestamp"] = pd.Timestamp(now)  
        output_file_name = "{}_V{:02.0f}.csv".format(pfafid,OUTPUT_VERSION)
        output_file_path = "{}/{}".format(ec2_output_path,output_file_name)
        df_basin.to_csv(output_file_path)
        print(output_file_path)

In [12]:
p= multiprocessing.Pool()
results_buffered = p.map(basin_to_csv,df_split)
p.close()
p.join()

/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//111011_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//145102_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//181976_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//142625_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//172497_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//232144_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//223940_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//155562_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//162203_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//127443_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//115801_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//153021_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//131902_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//122784_V02.csv
/volumes/data/Y2018M

/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//224002_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//131909_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//158115_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//127450_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//155571_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//122810_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//172524_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//145201_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//115808_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//111019_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//132930_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//162300_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//153028_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//142634_V02.csv
/volumes/data/Y2018M

/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//153034_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//172541_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//127467_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//132947_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//142642_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//145207_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//232230_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//111046_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//211011_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//162443_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//132170_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//225111_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//155579_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//116005_V02.csv
/volumes/data/Y2018M

/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//153042_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//111081_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//162450_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//132956_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//122853_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//145404_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//225118_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//158150_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//155617_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//117101_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//211018_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//232301_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//142652_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//172549_V02.csv
/volumes/data/Y2018M

/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//158218_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//155634_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//127493_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//111088_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//172557_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//232308_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//162468_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//145602_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//153049_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//142659_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//122870_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//211034_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//132242_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//225180_V02.csv
/volumes/data/Y2018M

...

/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//911109_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//742424_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//782705_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//812302_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//831951_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//772370_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//822478_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//652200_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//723060_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//753302_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//911211_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//712509_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//642451_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//725999_V02.csv
/volumes/data/Y2018M

/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//712606_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//831959_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//812309_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//822496_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//753309_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//742442_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//652208_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//723077_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//911240_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//642458_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//662908_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//742992_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//772406_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//782804_V02.csv
/volumes/data/Y2018M

/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//642466_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//742449_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//812472_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//723114_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//742999_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//713000_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//753408_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//664025_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//832105_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//726060_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//782920_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//772603_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//911270_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//652306_V02.csv
/volumes/data/Y2018M

/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//832422_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//782991_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//743007_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//753507_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//713226_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//742484_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//723150_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//726077_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//664044_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//911300_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//822541_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//812480_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//652404_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//772700_V02.csv
/volumes/data/Y2018M

/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//751205_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//822549_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//726087_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//652502_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//753625_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//742493_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//783000_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//832443_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//713280_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//812508_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//772808_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//751206_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//822550_V02.csv
/volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//726088_V02.csv
/volumes/data/Y2018M

In [13]:
!aws s3 cp {ec2_output_path} {s3_output_path} --recursive

upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/111014_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/111014_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/111013_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/111013_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/111011_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/111011_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/111020_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/111020_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/111017_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/111017_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/111016_V02.csv to s3://wri-projects/Aque

upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112020_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112020_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112014_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112014_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112030_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112030_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112019_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112019_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112041_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112041_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112042_V02.csv to s3://wri-projects/Aque

upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112809_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112809_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112901_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112901_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112904_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112904_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112805_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112805_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112902_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112902_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112903_V02.csv to s3://wri-projects/Aque

upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114417_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114417_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112807_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/112807_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114420_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114420_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114419_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114419_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114418_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114418_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114430_V02.csv to s3://wri-projects/Aque

upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114809_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114809_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114931_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114931_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114920_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114920_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114935_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114935_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114934_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114934_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/114808_V02.csv to s3://wri-projects/Aque

...

upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912103_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912103_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912101_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912101_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912104_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912104_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912102_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912102_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912106_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912106_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912108_V02.csv to s3://wri-projects/Aque

upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912704_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912704_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912705_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912705_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912578_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912578_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912706_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912706_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912708_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912708_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/912802_V02.csv to s3://wri-projects/Aque

upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/913479_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/913479_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/913476_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/913476_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/913478_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/913478_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/913480_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/913480_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/913490_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/913490_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/913300_V02.csv to s3://wri-projects/Aque

upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/913904_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/913904_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/913905_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/913905_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/913907_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/913907_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/914201_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/914201_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/914100_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/914100_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/914202_V02.csv to s3://wri-projects/Aque

upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/914805_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/914805_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/914806_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/914806_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/914709_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/914709_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/914803_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/914803_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/914807_V02.csv to s3://wri-projects/Aqueduct30/processData/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/914807_V02.csv
upload: ../../../../data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02/914804_V02.csv to s3://wri-projects/Aque

In [19]:
!gsutil -m cp \
{ec2_output_path}/*.csv \
{gcs_output_path}

Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//111011_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//111012_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//111013_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//111016_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//111017_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//111018_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//111019_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//111020_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//111030_V02.csv [Content-Type=text/

Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//112120_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//112140_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//112150_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//112300_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//112904_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//112907_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//112200_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//112700_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//112190_V02.csv [Content-Type=text/

Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//114443_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//114444_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//114445_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//114446_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//114447_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//114448_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//114449_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//114450_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//114460_V02.csv [Content-Type=text/

Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//115424_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//115425_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//115426_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//115427_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//115428_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//115429_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//115430_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//115440_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//115451_V02.csv [Content-Type=text/

Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//117107_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//117109_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//117108_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//117202_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//117201_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//117203_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//117204_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//117205_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//117206_V02.csv [Content-Type=text/

...

Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//832804_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//832805_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//832806_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//832807_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//832808_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//833001_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//832809_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//833000_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//832900_V02.csv [Content-Type=text/

Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//862097_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//862098_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//862099_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//863000_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//863001_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//863002_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//863003_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//863004_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//863005_V02.csv [Content-Type=text/

Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//912106_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//912107_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//912108_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//912109_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//912201_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//912202_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//912203_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//912204_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//912205_V02.csv [Content-Type=text/

Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//913445_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//913446_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//913447_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//913448_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//913449_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//913450_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//913460_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//913471_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//913472_V02.csv [Content-Type=text/

Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//914401_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//914402_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//914403_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//914404_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//914405_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//914406_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//914407_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//914408_V02.csv [Content-Type=text/csv]...
Copying file:///volumes/data/Y2018M07D17_RH_RDS_To_S3_V01/output_V02//914409_V02.csv [Content-Type=text/

In [14]:
end = datetime.datetime.now()
elapsed = end - start
print(elapsed)

0:24:27.818560
